# Тренировка моделей

## Подготовка

In [1]:
import pandas as pd
from sklearn.metrics import mean_squared_error as error_metric

from lets_plot import *
LetsPlot.setup_html()

import os; import sys; sys.path.append(os.path.join(sys.path[0], ".."))
from utils import misc as um
from utils import models as ums
from utils import transform_data as utd

In [2]:
DATA_DIR = "../data"
N_CLUSTERS = 5
N_CLUSTERS_MIN, N_CLUSTERS_MAX = 1, 10

In [3]:
char_widths_df = um.read_data("{0}/char_widths.csv".format(DATA_DIR), monospaced=False)

char_widths_df = utd.filter_by_font(char_widths_df, filters=["size", "face"])

print(char_widths_df.shape)
char_widths_df

(8240, 6)


char_id char  alphabet      subset      font_family  width
0          32          latin     symbols            Arial      5
1          32          latin     symbols          Calibri      6
2          32          latin     symbols         Garamond      6
3          32          latin     symbols           Geneva      6
4          32          latin     symbols          Georgia      6
...       ...  ...       ...         ...              ...    ...
8235     1327    ԯ  cyrillic  supplement        Helvetica     11
8236     1327    ԯ  cyrillic  supplement    Lucida Grande     11
8237     1327    ԯ  cyrillic  supplement         Rockwell     14
8238     1327    ԯ  cyrillic  supplement  Times New Roman     11
8239     1327    ԯ  cyrillic  supplement          Verdana     19

[8240 rows x 6 columns]

In [4]:
control_df = um.read_data("{0}/control.csv".format(DATA_DIR), monospaced=False)

train_control_df, test_control_df = utd.train_test_split_by_column(control_df, "text")

print(control_df.shape)
control_df

(242160, 8)


text  alphabet locale font_family  font_size  \
0       -0.09999999999999998  cyrillic  ru_RU       Arial          9   
1       -0.09999999999999998  cyrillic  ru_RU       Arial          9   
2       -0.09999999999999998  cyrillic  ru_RU       Arial          9   
3       -0.09999999999999998  cyrillic  ru_RU       Arial          9   
4       -0.09999999999999998  cyrillic  ru_RU       Arial         11   
...                      ...       ...    ...         ...        ...   
242155                 Ягода  cyrillic  ru_RU     Verdana         16   
242156                 Ягода  cyrillic  ru_RU     Verdana         20   
242157                 Ягода  cyrillic  ru_RU     Verdana         20   
242158                 Ягода  cyrillic  ru_RU     Verdana         20   
242159                 Ягода  cyrillic  ru_RU     Verdana         20   

          font_face  symbols_count  width  
0              bold             20    133  
1       bold+italic             20    133  
2            italic             20    134  
3            normal             20    133  
4              bold             20    153  
...             ...            ...    ...  
242155       normal              5     67  
242156         bold              5     93  
242157  bold+italic              5     93  
242158       italic              5     83  
242159       normal              5     83  

[242160 rows x 8 columns]

In [5]:
texts_df = um.read_data("{0}/texts.csv".format(DATA_DIR), monospaced=False)[["text", "alphabet"]].drop_duplicates()
print(texts_df.shape)
texts_df

(1033, 2)


text  alphabet
0                                    -0.04999999999999993  cyrillic
240                                  -0.04999999999999993     latin
1200                                 -0.09999999999999998  cyrillic
1440                                 -0.09999999999999998     latin
2400                                  -0.1499999999999999  cyrillic
...                                                   ...       ...
317760  Ученый обида коричневый другой устройство изме...  cyrillic
318000  Чем остановить освободить мотоцикл помолчать а...  cyrillic
318240                     Число ярко возможно прошептать  cyrillic
318480  Чувство блин карандаш легко самостоятельно куз...  cyrillic
318720                                              Ягода  cyrillic

[1033 rows x 2 columns]

In [6]:
char_df = pd.concat([
    ums.prepare_char_data(
        char_widths_df[char_widths_df.alphabet == alphabet],
        texts_df[texts_df.alphabet == alphabet].text
    ).assign(alphabet=lambda r: alphabet)
    for alphabet in char_widths_df.alphabet.unique()
])
print(char_df.shape)
char_df.head()

(824, 4)


width  weight  order alphabet
char                               
        5.8     813      4    latin
!       6.9       1     33    latin
"       8.5       1     62    latin
#      14.4       1    404    latin
$      11.5       1    176    latin

## Вычисление оптимального числа кластеров

In [7]:
clusters_train_df = utd.filter_by_font(train_control_df, filters=["size", "face"])
clusters_df = pd.DataFrame(columns=["n_clusters", "score"])
for n_clusters in range(N_CLUSTERS_MIN, N_CLUSTERS_MAX + 1):
    model = ums.ClusteringModel(
        calc_cluster_size=lambda r: r.width.mean(),
        clustering_col="width",
        n_clusters=n_clusters, random_state=42
    ).fit(char_df)
    clusters_df = pd.concat([clusters_df, pd.DataFrame({
        "n_clusters": [n_clusters],
        "score": [error_metric(clusters_train_df.width, model.predict(clusters_train_df.text))],
    })], ignore_index=True)
print(clusters_df.shape)
clusters_df

D:\anaconda3\envs\text-width-estimation\lib\site-packages\sklearn\cluster\_kmeans.py:1334: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=4.
  warnings.warn(
D:\anaconda3\envs\text-width-estimation\lib\site-packages\sklearn\cluster\_kmeans.py:1334: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=4.
  warnings.warn(
D:\anaconda3\envs\text-width-estimation\lib\site-packages\sklearn\cluster\_kmeans.py:1334: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=4.
  warnings.warn(
D:\anaconda3\envs\text-width-estimation\lib\site-packages\sklearn\cluster\_kmeans.py:1334: 

(10, 2)


n_clusters        score
0          1  2512.594423
1          2   429.053307
2          3   411.318418
3          4   248.299222
4          5   201.078729
5          6   208.955253
6          7   205.868093
7          8   179.565110
8          9   184.506485
9         10   194.834112

In [8]:
ggplot(clusters_df) + \
    geom_bar(aes(x="n_clusters", y="score"), stat='identity') + \
    scale_x_continuous(breaks=list(range(N_CLUSTERS_MIN, N_CLUSTERS_MAX + 1)))

## Тренировка и сохранение модели

In [9]:
ums.FullModel(
    clustering_model=ums.ClusteringModel(
        calc_cluster_size=lambda r: r.width.mean(),
        clustering_col="width",
        n_clusters=N_CLUSTERS, random_state=42
    ).fit(char_df)
).fit(train_control_df).save("{0}/model.csv".format(DATA_DIR), "{0}/model.json".format(DATA_DIR))
model = ums.FullModel.load("{0}/model.csv".format(DATA_DIR), "{0}/model.json".format(DATA_DIR))
model

D:\anaconda3\envs\text-width-estimation\lib\site-packages\sklearn\cluster\_kmeans.py:1334: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=4.
  warnings.warn(


Clusters:

mapOf(
0 to listOf(
' ', 'r', 'Î', 'Ï', 'l', 'j', 'i', 'f', 'ł', 'ŀ', '`', 'ľ', ']', '\', '¹', 'ļ', 'ĺ', 'ĵ', 'ı', 'İ', 'Í', 't', 'Ì', 'і', '¸', '·', 'ŧ', '´', '³', '²', '°', 'ť', 'ţ', 'į', 'ª', '¦', 'ř', 'ј', '¡', 'ŗ', 'ї', '|', 'ŕ', 'ſ', '¨', 'Į', '[', 'Ĭ', ';', ':', 'ĭ', 'ȷ', 'ț', '/', 'Ĩ', '.', ',', ')', '(', ''', '"', '!', '-', 'І', 'º', 'í', 'ï', 'I', 'î', 'Ī', 'ī', 'Ї', 'J', 'ì', 'ĩ'
),
1 to listOf(
'ś', 'ŝ', 'ş', 'ē', 'š', 'ĸ', 'ķ', 'Ŀ', 'Ĺ', 'Ť', 'Ĵ', 'ĳ', 'Ŧ', 'đ', 'ү', 'č', 'ұ', 'ũ', 'ҭ', 'Ţ', 'Ļ', 'ė', 'Ł', 'Ľ', 'ń', 'ħ', 'ņ', 'ғ', 'ĥ', 'Ȉ', 'ň', 'ģ', 'ґ', 'ŋ', 'Ґ', 'ġ', 'ğ', 'ō', 'ŏ', 'ő', 'ĝ', 'ě', 'ę', 'ĕ', 'ҝ', 'ћ', 'ŭ', 'Ј', 'ǃ', 'ǁ', 'ǀ', 'Г', 'З', 'Т', 'ƭ', 'ƫ', 'ƪ', 'а', 'б', 'в', 'г', 'д', 'Ѓ', 'е', 'Ǐ', 'ɍ', 'ȉ', 'Ȋ', 'ȋ', 'ǿ', 'ȑ', 'ȓ', 'ǻ', 'ș', 'ȝ', 'ǰ', 'ȴ', 'ȶ', 'ɂ', 'Ɉ', 'ɉ', 'ǐ', 'з', 'и', 'й', 'ѓ', 'є', 'ѕ', 'ž', 'ż', 'ź', 'ċ', 'Ÿ', 'ŷ', 'ќ', 'ў', 'ų', 'џ', 'ű', 'ů', 'ђ', 'ё', 'я', 'э', 'к', 'ƚ', 'л', 'Ɨ', 'Ɩ', 'н', 'о', 'ū', 'п', 'р', 'с', 'т',

## Оценка предсказаний

In [10]:
test_df = test_control_df.copy()
test_df["non_exaggerated_prediction"] = model.predict(test_df, use_exagg=False).round().astype(int)
test_df["non_exaggerated_prediction_error"] = test_df.non_exaggerated_prediction - test_df.width
test_df["non_exaggerated_prediction_mean_error"] = test_df.non_exaggerated_prediction_error / test_df.symbols_count
test_df["exaggerated_prediction"] = model.predict(test_df, use_exagg=True).round().astype(int)
test_df["exaggerated_prediction_error"] = test_df.exaggerated_prediction - test_df.width
test_df["exaggerated_prediction_mean_error"] = test_df.exaggerated_prediction_error / test_df.symbols_count
print(test_df.shape)
test_df

(57120, 14)


text  alphabet locale font_family  font_size  \
0      -0.19999999999999996  cyrillic  ru_RU       Arial          9   
1      -0.19999999999999996  cyrillic  ru_RU       Arial          9   
2      -0.19999999999999996  cyrillic  ru_RU       Arial          9   
3      -0.19999999999999996  cyrillic  ru_RU       Arial          9   
4      -0.19999999999999996  cyrillic  ru_RU       Arial         11   
...                     ...       ...    ...         ...        ...   
57115       Чувство дыхание  cyrillic  ru_RU     Verdana         16   
57116       Чувство дыхание  cyrillic  ru_RU     Verdana         20   
57117       Чувство дыхание  cyrillic  ru_RU     Verdana         20   
57118       Чувство дыхание  cyrillic  ru_RU     Verdana         20   
57119       Чувство дыхание  cyrillic  ru_RU     Verdana         20   

         font_face  symbols_count  width  non_exaggerated_prediction  \
0             bold             20    133                         140   
1      bold+italic             20    133                         141   
2           italic             20    134                         129   
3           normal             20    133                         127   
4             bold             20    153                         171   
...            ...            ...    ...                         ...   
57115       normal             15    197                         201   
57116         bold             15    269                         273   
57117  bold+italic             15    270                         275   
57118       italic             15    242                         254   
57119       normal             15    242                         251   

       non_exaggerated_prediction_error  \
0                                     7   
1                                     8   
2                                    -5   
3                                    -6   
4                                    18   
...                                 ...   
57115                                 4   
57116                                 4   
57117                                 5   
57118                                12   
57119                                 9   

       non_exaggerated_prediction_mean_error  exaggerated_prediction  \
0                                   0.350000                     154   
1                                   0.400000                     156   
2                                  -0.250000                     142   
3                                  -0.300000                     140   
4                                   0.900000                     188   
...                                      ...                     ...   
57115                               0.266667                     222   
57116                               0.266667                     301   
57117                               0.333333                     303   
57118                               0.800000                     280   
57119                               0.600000                     277   

       exaggerated_prediction_error  exaggerated_prediction_mean_error  
0                                21                           1.050000  
1                                23                           1.150000  
2                                 8                           0.400000  
3                                 7                           0.350000  
4                                35                           1.750000  
...                             ...                                ...  
57115                            25                           1.666667  
57116                            32                           2.133333  
57117                            33                           2.200000  
57118                            38                           2.533333  
57119                            35                           2.333333  

[57120 rows x 14 columns]

In [11]:
ggplot(test_df) + \
    geom_point(aes("width", "non_exaggerated_prediction", color="alphabet"), alpha=.3) + \
    geom_abline(slope=1, color="magenta") + \
    facet_wrap(facets="font_family", ncol=3) + \
    ggtitle("Соотношение ширины и предсказания для скорректированной по шрифту модели")

In [12]:
ggplot(test_df) + \
    geom_point(aes("width", "exaggerated_prediction", color="alphabet"), alpha=.3) + \
    geom_abline(slope=1, color="magenta") + \
    facet_wrap(facets="font_family", ncol=3) + \
    ggtitle("Соотношение ширины и предсказания для преувеличивающей модели")

In [13]:
ggplot(test_df) + \
    geom_density(aes("non_exaggerated_prediction_mean_error")) + \
    facet_wrap(facets="font_family", ncol=3) + \
    ggtitle("Распределение средней ошибки для скорректированной по шрифту модели")

In [14]:
ggplot(test_df) + \
    geom_density(aes("exaggerated_prediction_mean_error")) + \
    facet_wrap(facets="font_family", ncol=3) + \
    ggtitle("Распределение средней ошибки для преувеличивающей модели")